In [2]:
import pandas as pd
import numpy as np
import datetime, requests, os, json

In [3]:
def get_specific_btc_block_json(block_id):
    url = 'https://blockchain.info/rawblock/' + str(block_id)
    r = requests.get(url=url)
    return r.json()

# TEST START ---------------------------------
request_json_60k = get_specific_btc_block_json(60000)
request_json_600k = get_specific_btc_block_json(600000)


In [74]:
request_json_700k = get_specific_btc_block_json(700000)

In [4]:
print(request_json_60k['hash'] == '000000000b554c46f8eb7264d7d5e334382c6fc3098dabf734de37962ccd7495')
# TEST END ---------------------------------

def parse_n_add_block_header(file_path, block_data):
    # Slicing off trx from block json
    block_header = {key:val for key, val in block_data.items() if type(val) is not list}
    # Convert to df
    df = pd.DataFrame(block_header, index=[0])
    if os.path.exists(file_path): # If file exists
        # Add to existing csv (create if not existing)
        df.to_csv(file_path, mode='a', index=False, header=False)
    else: # If file not yet existing, create
        df.to_csv(file_path, index=False, header=True)

# TEST START ---------------------------------
file_path = '/Users/sachaschwab/Dropbox/Projects/Blockchain Analytics/blk_headers_test.csv'
# Make sure text.csv not yet existing. Accept if two same lines in file
if os.path.exists(file_path):
    os.remove(file_path)
parse_n_add_block_header(file_path=file_path, block_data=request_json_60k)
parse_n_add_block_header(file_path=file_path, block_data=request_json_60k)
df_test = pd.read_csv(file_path)
print(len(df_test) == 2 )
#print(df_test.iloc[0] == df_test.iloc[1])
print(df_test['hash'][0] == df_test['hash'][1])
# TEST END ---------------------------------

def parse_n_add_tx(file_path_headers, file_path_in_out, block_data):
    # --------- Parsing Tx headers -------------------
    df_tx_headers = pd.DataFrame()
    for tx_item in block_data['tx']:
        # dict comprehension over items
        trx_header = {key:val for key, val in tx_item.items() if type(val) is not list}
        # convert dict to df
        df = pd.DataFrame(trx_header, index=[0])
        df_tx_headers = pd.concat([df_tx_headers, df], ignore_index=True)

    if os.path.exists(file_path): # If file exists
        # Add to existing csv (create if not existing)
        df_tx_headers.to_csv(file_path, mode='a', index=False, header=False)
    else: # If file not yet existing, create
        df_tx_headers.to_csv(file_path, index=False, header=True)

    # --------- Parsing Tx inputs -------------------
    

    # --------- Parsing Tx outputs -------------------




# TEST START ---------------------------------
file_path_headers = '/Users/sachaschwab/Dropbox/Projects/Blockchain Analytics/tx_headers_test.csv'
file_path_in_out = '/Users/sachaschwab/Dropbox/Projects/Blockchain Analytics/tx_in_out_test.csv'
if os.path.exists(file_path_headers):
    os.remove(file_path_headers)
if os.path.exists(file_path_in_out):
    os.remove(file_path_in_out)
parse_n_add_tx(file_path_headers, file_path_in_out, request_json_60k)
df_headers_test = pd.read_csv(file_path_headers)
df_in_out_test = pd.read_csv(file_path_in_out)
print(df_headers_test.iloc[-1]['hash'] == 'f0215df69bd55e44acd06c54a21ef671619e6ddc2fadbf659a48587cf343b1af')
print(df_in_out_test.iloc[-1]) # Todo: finalise test logic
# TEST END ---------------------------------


True
True
True
True


In [110]:
inp = request_json_600k['tx'][6]['inputs']
inp

[{'sequence': 4294967295,
  'witness': '',
  'script': '473044022062a50c4373f0cad58787a4449e0a63a1cd19abe36a0e002a54487ff27d813668022026401ea091ac26bd09a2947acbe7a2b638cb2b98da19dc6c0e36de80a96430e90121039f843adf502df5c13c5f3a851a76bd9de980fbc63a84864b8d70a471030f7520',
  'index': 0,
  'prev_out': {'tx_index': 900199672572093,
   'value': 546,
   'n': 1,
   'type': 0,
   'spent': True,
   'script': '76a914ea3117186db5e339a51fd89c1a8b8034b58df80288ac',
   'spending_outpoints': [{'tx_index': 3165718108226998, 'n': 0}],
   'addr': '1NMHvji73ua1urSj3EhMZiXsDYaE32yuV2'}},
 {'sequence': 4294967295,
  'witness': '',
  'script': '4730440220237437d1719d306fe99908ad2fd7e94ed87ec3a21cf7355b7c8ed46dbc657ef80220357973d0e4adfc433d48c9a9cfc0bc904753b229c2d9cfea918d5149f33a6b9701210359cbe88d65ad41b11fc97979cd916d929bfd98ac8d37db6954bbf3c7d98f6426',
  'index': 1,
  'prev_out': {'tx_index': 1039080567694970,
   'value': 208787,
   'n': 0,
   'type': 0,
   'spent': True,
   'script': '76a9140141e36f27f61

In [150]:
inp_0 = inp[0]
# Disregarding keys: witness, script
relevant_keys = {'sequence', 'index'}
input_header = {key: inp_0[key] for key in inp_0.keys() & relevant_keys}
input_header

{'index': 0, 'sequence': 4294967295}

In [130]:
inp_0['prev_out']

{'tx_index': 900199672572093,
 'value': 546,
 'n': 1,
 'type': 0,
 'spent': True,
 'script': '76a914ea3117186db5e339a51fd89c1a8b8034b58df80288ac',
 'spending_outpoints': [{'tx_index': 3165718108226998, 'n': 0}],
 'addr': '1NMHvji73ua1urSj3EhMZiXsDYaE32yuV2'}

In [161]:
# Disregarding keys: witness, script
relevant_keys = {'tx_index', 'addr', 'value'}
prev_out = {key: inp_0['prev_out'][key] for key in inp_0['prev_out'].keys() & relevant_keys}
prev_out['prev_tx_index'] = prev_out.pop('tx_index')
prev_out

{'value': 546,
 'addr': '1NMHvji73ua1urSj3EhMZiXsDYaE32yuV2',
 'prev_tx_index': 900199672572093}

In [162]:
inp_0['prev_out']['spending_outpoints'][0]

{'tx_index': 3165718108226998, 'n': 0}

In [163]:
relevant_keys = ['tx_index']
spend_out = {key: inp_0['prev_out']['spending_outpoints'][0][key] for key in inp_0['prev_out']['spending_outpoints'][0].keys() & relevant_keys}
spend_out

{'tx_index': 3165718108226998}

In [167]:
inps = input_header.copy()
inps.update(prev_out)
inps.update(spend_out)
inps

{'index': 0,
 'sequence': 4294967295,
 'value': 546,
 'addr': '1NMHvji73ua1urSj3EhMZiXsDYaE32yuV2',
 'prev_tx_index': 900199672572093,
 'tx_index': 3165718108226998}

In [73]:
ins = pd.DataFrame(columns=['sequence', 'witness', 'script', 'index', 'prev_out'])

trx_header = {}

for trx in request_json_600k['tx']:
    for input in trx['inputs']:
        # We gather the fields, first up
        trx_header = {key:val for key, val in input.items() if type(val) is not dict}
        # This gives us the fields without 'prev_out', i.e.
        # {'sequence','witness', 'script', 'index'}
        # Then, prev_out, first part:
        prev_out = input['prev_out']
        prev_out_1 = {key:val for key, val in input.items() if type(val) is not dict}
        # This gives us the following fields, here in an example:
        # 'tx_index': 0, 'value': 0, 'n': 4294967295, 'type': 0, 'spent': True, 'script': '', 
        # 'spending_outpoints': [{'tx_index': 5745043599214769, 'n': 0}]
        # So, we need to continue parsing, with spending_outpoints
        # Luckily spending_outpoints always only has 1 entry
        tx_index = prev_out['spending_outpoints'][0]['tx_index']
        print(tx_index)
    break

{'tx_index': 0, 'value': 0, 'n': 4294967295, 'type': 0, 'spent': True, 'script': '', 'spending_outpoints': [{'tx_index': 5745043599214769, 'n': 0}]}
5745043599214769


In [75]:
request_json_700k

{'hash': '0000000000000000000590fc0f3eba193a278534220b2b37e9849e1a770ca959',
 'ver': 1073733636,
 'prev_block': '0000000000000000000aa3ce000eb559f4143be419108134e0ce71042fc636eb',
 'mrkl_root': '1f8d213c864bfe9fb0098cecc3165cce407de88413741b0300d56ea0f4ec9c65',
 'time': 1631333672,
 'bits': 386877668,
 'next_block': ['00000000000000000002f39baabb00ffeb47dbdb425d5077baa62c47482b7e92'],
 'fee': 15388640,
 'nonce': 2881644503,
 'n_tx': 1276,
 'size': 1276422,
 'block_index': 700000,
 'main_chain': True,
 'height': 700000,
 'weight': 3998094,
 'tx': [{'hash': '1d8149eb8d8475b98113b5011cf70e0b7a4dccff71286d28b8b4b641f94f1e46',
   'ver': 1,
   'vin_sz': 1,
   'vout_sz': 3,
   'size': 312,
   'weight': 1140,
   'fee': 0,
   'relayed_by': '0.0.0.0',
   'lock_time': 1028092026,
   'tx_index': 2467072150353622,
   'double_spend': False,
   'time': 1631333672,
   'block_index': 700000,
   'block_height': 700000,
   'inputs': [{'sequence': 0,
     'witness': '01200000000000000000000000000000000000

In [32]:
n_tx = request_json['n_tx']
df_tx_headers = pd.DataFrame.from_dict(request_json['tx'])
df_tx_headers.head()

hash  ver  vin_sz  vout_sz  \
0  93955d40d918d014903843d258aada5c720a5d37afac78...    1       1        2   
1  a8178a7223372414ac060b4bba4b33b8b4847a756fa76a...    2       1        3   
2  efb3f60304532ebc80163b5f375fa8a94a39a8b0807b99...    2       5        2   
3  a070eda356c87a7af9bff22eab3b3c38460605eb00938c...    2       2        2   
4  b96b516295b8e4f5452405db8213ca56cde630b7a30c2a...    2       1        2   

   size  weight     fee relayed_by  lock_time          tx_index  double_spend  \
0   200     692       0    0.0.0.0          0  5745043599214769         False   
1   290    1160  100000    0.0.0.0          0  7503592271527870         False   
2   910    2341  117400    0.0.0.0     599998  6753953176718477         False   
3   399    1266   50880    0.0.0.0     599999  4239768503034797         False   
4   249     669   16800    0.0.0.0     599983  1478774222172713         False   

         time  block_index  block_height  \
0  1571443461       600000        600000   
1  1571443461       600000        600000   
2  1571443461       600000        600000   
3  1571443461       600000        600000   
4  1571443461       600000        600000   

                                              inputs  \
0  [{'sequence': 4294967295, 'witness': '01200000...   
1  [{'sequence': 4294967295, 'witness': '', 'scri...   
2  [{'sequence': 4294967294, 'witness': '', 'scri...   
3  [{'sequence': 4294967294, 'witness': '', 'scri...   
4  [{'sequence': 4294967293, 'witness': '02473044...   

                                                 out  
0  [{'type': 0, 'spent': True, 'value': 125376404...  
1  [{'type': 0, 'spent': True, 'value': 795759, '...  
2  [{'type': 0, 'spent': True, 'value': 882998, '...  
3  [{'type': 0, 'spent': True, 'value': 1111362, ...  
4  [{'type': 0, 'spent': True, 'value': 50000, 's...

Empty DataFrame
Columns: [hash, ver, prev_block, mrkl_root, time, bits, fee, nonce, n_tx, size, block_index, main_chain, height, weight]
Index: []

In [ ]:
# Extract block base info + transactions

# Set up first heuristics



In [ ]:
start_end_blk = [200000, 2000002]
def main():
    if len(start_end_blk) == 2: # keep array empty if using node data
        blocks_to_parse = np.arange(start_end_blk[0], start_end_blk[1])
    else: # node data
        return(None)
    


In [166]:
request_json_600k

{'hash': '00000000000000000007316856900e76b4f7a9139cfbfba89842c8d196cd5f91',
 'ver': 536870912,
 'prev_block': '00000000000000000003ecd827f336c6971f6f77a0b9fba362398dd867975645',
 'mrkl_root': '66b7c4a1926b41ceb2e617ddae0067e7bfea42db502017fde5b695a50384ed26',
 'time': 1571443461,
 'bits': 387294044,
 'next_block': ['00000000000000000000817313d6b5fe4838ec6eff47fbe7c4b9f22a40c2a4f4'],
 'fee': 3764047,
 'nonce': 1066642855,
 'n_tx': 1925,
 'size': 870371,
 'block_index': 600000,
 'main_chain': True,
 'height': 600000,
 'weight': 2848472,
 'tx': [{'hash': '93955d40d918d014903843d258aada5c720a5d37afac7889268f459a97b148a3',
   'ver': 1,
   'vin_sz': 1,
   'vout_sz': 2,
   'size': 200,
   'weight': 692,
   'fee': 0,
   'relayed_by': '0.0.0.0',
   'lock_time': 0,
   'tx_index': 5745043599214769,
   'double_spend': False,
   'time': 1571443461,
   'block_index': 600000,
   'block_height': 600000,
   'inputs': [{'sequence': 4294967295,
     'witness': '012000000000000000000000000000000000000000